In [1]:
# NBVAL_SKIP
from openff.toolkit.typing.engines.smirnoff import forcefield
from openff.toolkit.typing.engines.smirnoff import forcefield_utils as ff_utils
from simtk import openmm
from simtk.openmm import XmlSerializer
from simtk.openmm import app
from simtk import unit
from openmoltools import system_checker
import parmed
import openeye.oechem as oechem
from simtk.openmm.app import PDBFile

In [2]:
# NBVAL_SKIP
pdbfile = PDBFile('cyclohexane_ethanol_0.4_0.6.pdb')
ff = forcefield.ForceField('forcefield/Frosst_AlkEthOH.offxml')

mols = []
flavor = oechem.OEIFlavor_Generic_Default | oechem.OEIFlavor_MOL2_Default | oechem.OEIFlavor_MOL2_Forcefield
for molname in ['cyclohexane', 'ethanol']:
    ifs = oechem.oemolistream(molname+'.mol2')
    ifs.SetFlavor( oechem.OEFormat_MOL2, flavor)
    mol = oechem.OEGraphMol()
    while oechem.OEReadMolecule(ifs, mol):
        oechem.OETriposAtomNames(mol)
        mols.append(oechem.OEGraphMol(mol))

#system = ff.createSystem( pdbfile.topology, mols)
system = ff.createSystem( pdbfile.topology, mols, chargeMethod='OECharges_AM1BCCSym')
#Swap in positions
integrator = openmm.VerletIntegrator(1.0 * unit.femtoseconds)
context = openmm.Context(system, integrator)
context.setPositions(pdbfile.positions)

# Create parmed Structure
structure = parmed.openmm.topsystem.load_topology( pdbfile.topology, system, pdbfile.positions)
# Write AMBER parameter/crd
#parmed.amber.AmberParm( system, structure)
#help(structure.save)
#Save prmtop
structure.save('system.prmtop', overwrite=True)
# Save crd
structure.save('system.crd', format='rst7', overwrite=True)

# Save in GROMACS too
structure.save('system.gro', overwrite = True)
structure.save('system.top', overwrite=True, format='gromacs')

In [3]:
# NBVAL_SKIP
# Evaluate energy of OpenMM system and AMBER system to check that they are still the same
parm = parmed.load_file('system.prmtop', 'system.crd')
ambersys = parm.createSystem(nonbondedMethod= app.NoCutoff, constraints = None, implicitSolvent = None)
groups0, groups1, energy0, energy1 = ff_utils.compare_system_energies( pdbfile.topology, pdbfile.topology, ambersys, system, pdbfile.positions)

Num (type) 	 Num (type) 	 Num (type) 	 Num (type) 	 per 	 phase 	 k0
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 55 ( C2)-  54 ( C1)- 	 59 ( C6)- 	  58 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 55 ( C2)-  54 ( C1)- 	 59 ( C6)- 	  58 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 55 ( C2)-  54 ( C1)- 	 59 ( 

In [4]:
# NBVAL_SKIP
# Dump OpenMM systems out

# Do Open Force Field system
serialized_system_smirff = XmlSerializer.serialize(system)
outfile = open('openforcefield_system.xml','w')
outfile.write(serialized_system_smirff)
outfile.close()
# Do amber system
serialized_system_amber = XmlSerializer.serialize(ambersys)
outfile = open('amber_system.xml','w')
outfile.write(serialized_system_amber)
outfile.close()

In [5]:
# NBVAL_SKIP
# deserialize systems and confirm energies still different without using external tools
smirff_system = XmlSerializer.deserialize(serialized_system_smirff)
amber_system = XmlSerializer.deserialize(serialized_system_amber)
pdbfile = PDBFile('cyclohexane_ethanol_0.4_0.6.pdb')

# Do an energy comparison
timestep = 1.0 * unit.femtoseconds
integrator0 = openmm.VerletIntegrator( timestep )
integrator1 = openmm.VerletIntegrator( timestep )
platform = openmm.Platform.getPlatformByName("Reference")
positions = pdbfile.positions
simulation0 = app.Simulation( pdbfile.topology, smirff_system, integrator0, platform = platform )
simulation0.context.setPositions(positions)
simulation1 = app.Simulation( parm.topology, amber_system, integrator1, platform = platform )
simulation1.context.setPositions(positions)
syscheck = system_checker.SystemChecker( simulation0, simulation1 )
groups0, groups1 = syscheck.check_energy_groups(skip_assert = False)
energy0, energy1 = syscheck.check_energies(skip_assert = False)

In [6]:
# NBVAL_SKIP
# One more test - use new Open Force Field functions to take system, save to AMBER/GROMACS, re-load and check energy

pdbfile = PDBFile('cyclohexane_ethanol_0.4_0.6.pdb')

#Save systems
ff_utils.save_system_to_amber( pdbfile.topology, system, pdbfile.positions, 'out.prmtop', 'out.crd')
ff_utils.save_system_to_gromacs( pdbfile.topology, system, pdbfile.positions, 'out.top', 'out.gro')

# Load and check energies - amber
parm = parmed.load_file('out.prmtop', 'out.crd')
#ambersys = parm.createSystem(nonbondedMethod= app.NoCutoff, constraints = None, implicitSolvent = None)
groups0, groups1, energy0, energy1 = ff_utils.compare_system_energies( pdbfile.topology, pdbfile.topology, ambersys, system, pdbfile.positions)

# Load and check energies - gromacs
top = parmed.load_file('out.top')
gro = parmed.load_file('out.gro')
gromacssys = top.createSystem(nonbondedMethod= app.NoCutoff, constraints = None, implicitSolvent = None)
groups0, groups1, energy0, energy1 = ff_utils.compare_system_energies( pdbfile.topology, pdbfile.topology, gromacssys, system, pdbfile.positions)


Num (type) 	 Num (type) 	 Num (type) 	 Num (type) 	 per 	 phase 	 k0
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 19 ( C2)-  18 ( C1)- 	 23 ( C6)- 	  22 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 37 ( C2)-  36 ( C1)- 	 41 ( C6)- 	  40 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
 55 ( C2)-  54 ( C1)- 	 59 ( C6)- 	  58 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
 55 ( C2)-  54 ( C1)- 	 59 ( C6)- 	  58 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
 55 ( C2)-  54 ( C1)- 	 59 ( 

In [7]:
# NBVAL_SKIP
# Let's round trip the AMBER system to double check the issue one more time
ff_utils.save_system_to_gromacs( pdbfile.topology, ambersys, pdbfile.positions, 'out2.top', 'out2.gro')
top = parmed.load_file('out2.top')
gro = parmed.load_file('out2.gro')
gromacssys = top.createSystem(nonbondedMethod= app.NoCutoff, constraints = None, implicitSolvent = None)
groups0, groups1, energy0, energy1 = ff_utils.compare_system_energies( pdbfile.topology, pdbfile.topology, gromacssys, ambersys, pdbfile.positions)


Num (type) 	 Num (type) 	 Num (type) 	 Num (type) 	 per 	 phase 	 k0
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
  1 ( C2)-   0 ( C1)- 	 5 ( C6)- 	   4 ( C5)- 	 1.000000 	 180.000000 	 0.836800 
  5 ( C6)-   0 ( C1)- 	 1 ( C2)- 	   2 ( C3)- 	 3.000000 	 0.000000 	 0.753120 
  5 ( C6)-   0 ( C1)- 	 1 ( C2)- 	   2 ( C3)- 	 2.000000 	 180.000000 	 1.046000 
  5 ( C6)-   0 ( C1)- 	 1 ( C2)- 	   2 ( C3)- 	 1.000000 	 180.000000 	 0.836800 
  0 ( C1)-   1 ( C2)- 	 2 ( C3)- 	   3 ( C4)- 	 3.000000 	 0.000000 	 0.753120 
  0 ( C1)-   1 ( C2)- 	 2 ( C3)- 	   3 ( C4)- 	 2.000000 	 180.000000 	 1.046000 
  0 ( C1)-   1 ( C2)- 	 2 ( C3)- 	   3 ( C4)- 	 1.000000 	 180.000000 	 0.836800 
  1 ( C2)-   2 ( C3)- 	 3 ( C4)- 	   4 ( C5)- 	 3.000000 	 0.000000 	 0.753120 
  1 ( C2)-   2 ( C3)- 	 3 ( C4)- 	   4 ( C5)- 	 2.000000 	 180.000000 	 1.046000 
  1 ( C2)-   2 ( C3)- 	 3 ( C4)- 	   

In [8]:
# NBVAL_SKIP
# Amber system
parm = parmed.load_file('out.prmtop', 'out.crd')
print(parmed.openmm.energy_decomposition_system(parm, parm.createSystem()))

# Gromacs system for cross-checking
top = parmed.gromacs.GromacsTopologyFile('out2.top')
top.positions = parm.positions
print(parmed.openmm.energy_decomposition_system(top, top.createSystem()))


[('HarmonicBondForce', 42.564366981529595), ('HarmonicAngleForce', 109.54929960189996), ('PeriodicTorsionForce', 381.41868462924975), ('NonbondedForce', 12146.742154571653), ('CMMotionRemover', 0.0)]
[('HarmonicBondForce', 42.564366986426606), ('HarmonicAngleForce', 109.5492997853153), ('PeriodicTorsionForce', 381.4186855481072), ('NonbondedForce', 12146.749589588657), ('CMMotionRemover', 0.0)]
